In [1]:
import NeuroSAT
import torch
import pickle
import explainer_NeuroSAT
import datasetLoader
import wandb

In [3]:
opts = {
        'out_dir': '/Users/trist/Documents/Bachelor-Thesis/NeuroSAT/test/files/data/dataset_train_8_size4000',
        'logging': '/Users/trist/Documents/Bachelor-Thesis/NeuroSAT/test/files/log/dataset_train_8_size4000.log',
        'val_reals_dir': '/Users/trist/Documents/Bachelor-Thesis/NeuroSAT/test/files/data/dataset_train_8_size4000_val_reals',
        'test_reals_dir': '/Users/trist/Documents/Bachelor-Thesis/NeuroSAT/test/files/data/dataset_train_8_size4000_test_reals',
        'val_gt_edges_per_problem': '/Users/trist/Documents/Bachelor-Thesis/NeuroSAT/test/files/data/dataset_train_8_size4000_val_gt_edges_per_problem',
        'test_gt_edges_per_problem': '/Users/trist/Documents/Bachelor-Thesis/NeuroSAT/test/files/data/dataset_train_8_size4000_test_gt_edges_per_problem',
        'n_pairs': 100,  # Anzahl der zu generierenden Paare
        'min_n': 8,
        'max_n': 8,
        'p_k_2': 0.3,
        'p_geo': 0.4,
        'max_nodes_per_batch': 4000,
        'one_pair': False,
        'emb_dim': 128,
        'iterations': 26,
    }

device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

## Smaller problem

In [3]:
opts = {
        'out_dir': '/Users/trist/Documents/Bachelor-Thesis/NeuroSAT/test/files/data/dataset_train_8_size500',
        'logging': '/Users/trist/Documents/Bachelor-Thesis/NeuroSAT/test/files/log/dataset_train_8_size500.log',
        'reals_dir': '/Users/trist/Documents/Bachelor-Thesis/NeuroSAT/test/files/data/dataset_train_8_size500_reals',
        'gt_edges_per_problem': '/Users/trist/Documents/Bachelor-Thesis/NeuroSAT/test/files/data/dataset_train_8_size500_gt_edges_per_problem',
        'n_pairs': 20,  # Anzahl der zu generierenden Paare
        'min_n': 8,
        'max_n': 8,
        'p_k_2': 0.3,
        'p_geo': 0.4,
        'max_nodes_per_batch': 500,
        'one_pair': False,
        'emb_dim': 128,
        'iterations': 26,
    }

device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

## Generate GT for problem

In [5]:
data = datasetLoader.loadSatBatches(opts['out_dir'])

#print(len(data[2].is_sat))
datasetLoader.storeGTforData(data[-2], opts['min_n'], opts['out_dir']+'_val')

#with open(opts['reals_dir'], 'rb') as file:
#        reals = pickle.load(file)

In [5]:
from torch_geometric import seed
import utils
import wandb
import torch.nn.functional as fn
from torcheval.metrics.functional import binary_auroc
from collections import defaultdict
from kneed import KneeLocator


def trainExplainer (datasetName, opts, save_model=False, wandb_project="Explainer-NeuroSAT", runSeed=None) :
    if runSeed is not None: seed.seed_everything(runSeed)
    
    device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
    
    # Check valid dataset name
    configOG = utils.loadConfig(datasetName)
    if configOG == -1:
        return
    
    params = configOG['params']
    graph_task = params['graph_task']
    epochs = params['epochs']
    t0 = params['t0']
    tT = params['tT']
    sampled_graphs = params['sampled_graphs']
    coefficient_size_reg = params['coefficient_size_reg']
    coefficient_entropy_reg = params['coefficient_entropy_reg']
    coefficient_L2_reg = params['coefficient_L2_reg']
    coefficient_consistency = params['coefficient_consistency']
    num_explanation_edges = params['num_explanation_edges']
    lr_mlp = params['lr_mlp']

    wandb.init(project=wandb_project, config=params)

    hidden_dim = 64 # Make loading possible
    clip_grad_norm = 2 # Make loading possible
    min_clip_value = -2
    
    with open(opts['out_dir'], 'rb') as file:
        data = pickle.load(file)
    
    # TODO: Split data into train and test
    # TODO: !!! each data consist of multiple problems !!! -> Extract singular problems for calculating the loss!
    dataset = data
    
    eval_problem = data[-2]
    test_problem = data[-1]
    
    with open(opts['reals_dir'], 'rb') as file:
        reals = pickle.load(file)
        
    with open(opts['gt_edges_per_problem'], 'rb') as file:
        gt_edges_per_problem = pickle.load(file)
    

    downstreamTask = NeuroSAT.NeuroSAT(opts=opts,device=device)
    checkpoint = torch.load(f"models/neurosat_sr10to40_ep1024_nr26_d128_last.pth.tar", weights_only=True, map_location=device)
    downstreamTask.load_state_dict(checkpoint['state_dict'])

    mlp = explainer_NeuroSAT.MLP_SAT(GraphTask=graph_task).to(device)
    wandb.watch(mlp, log= "all", log_freq=2, log_graph=False)

    mlp_optimizer = torch.optim.Adam(params = mlp.parameters(), lr = lr_mlp)

    downstreamTask.eval()
    for param in downstreamTask.parameters():
        param.requires_grad = False

    eval_pred, _, _, _ = downstreamTask.forward(eval_problem)
    eval_pred_bin = eval_pred > 0.5
    acc = (eval_pred_bin == torch.tensor(eval_problem.is_sat)).float().mean()
    print(f"Downstream task accuracy on eval problem: {acc.item()}")

    training_iterator = dataset
    
    for epoch in range(0, epochs) :
        mlp.train()
        mlp_optimizer.zero_grad()

        temperature = t0*((tT/t0) ** ((epoch+1)/epochs))
        
        #sampledEdges = 0.0
        #sumSampledEdges = 0.0
        
        #samplePredSum = 0

        for index, content in enumerate(training_iterator):
            # stop training before last batch, used for evaluation
            if index == len(training_iterator)-2: break
            # stop training after first batch
            #if index > 0: break
            node_to_predict = None
            if graph_task: 
                # !! current_problem is really a batch of problems !!
                current_problem = content

            # MLP forward
            # TODO: Implement embeddingCalculation for SAT
            w_ij, unique_clauses, inverse_indices = mlp.forward(downstreamTask, current_problem, nodeToPred=node_to_predict)

            sampleLoss = torch.FloatTensor([0]).to(device)
            loss = torch.FloatTensor([0]).to(device)
            
            pOriginal, _, _, _ = downstreamTask.forward(current_problem)
            pOriginal = fn.softmax(pOriginal, dim=0)
            
            #pOriginal = torch.tensor([1 - pOriginal, pOriginal])
            
            for k in range(0, sampled_graphs):
                edge_ij = mlp.sampleGraph(w_ij, unique_clauses, inverse_indices, temperature)
            
                # TODO: softmax needed for loss, beacuse negative values do not work with log! Need for normalization?
                pSample, _, _, _ = downstreamTask.forward(current_problem, edge_weights=edge_ij)
                pSample = fn.softmax(pSample, dim=0)
                #pSample = torch.tensor([1 - pSample, pSample])
                
                if graph_task:
                    """for sub_problem_idx in range(len(current_problem.is_sat)):
                        # batch_mask needed to differentiate sub_problems in batch of problems for loss
                        # batch_edges cannot simply be divided since sub_problems have different number of edges/clauses
                        # IMPORTANT: batch_size and n variables dependant on data!!
                        batch_mask = utils.get_batch_mask(torch.tensor(current_problem.batch_edges), sub_problem_idx, opts['min_n'], current_problem.n_variables)
                        #(pOriginal[sub_problem_idx] >= 0.5).int()
                        currLoss = mlp.loss(pOriginal[sub_problem_idx], pSample[sub_problem_idx], edge_ij[batch_mask], current_problem.batch_edges[batch_mask], coefficient_size_reg, coefficient_entropy_reg, coefficientConsistency=coefficient_consistency)
                        sampleLoss.add_(currLoss)"""
                    currLoss = mlp.loss(pOriginal, pSample, edge_ij, current_problem.batch_edges, coefficient_size_reg, coefficient_entropy_reg, coefficientConsistency=coefficient_consistency, bce=True)
                    sampleLoss.add_(currLoss)
                    

            loss += sampleLoss / sampled_graphs
            
            #sumSampledEdges += sampledEdges / sampled_graphs

        #print(samplePredSum)
        
        loss = loss / len(training_iterator)
        loss.backward()
        
        mlp_optimizer.step()

        print(f"Epoch {epoch+1}, Loss: {loss.item()}")

        torch.nn.utils.clip_grad_norm_(mlp.parameters(), max_norm=clip_grad_norm)
        
        """for param in mlp.parameters():
            if param.grad is not None:
                param.grad.data = torch.max(param.grad.data, min_clip_value * torch.ones_like(param.grad.data))"""

        mlp.eval()
        
        """if graph_task:
            #TODO: Evaluation for SAT! Needs gt
            meanAuc = evaluation.evaluateNeuroSATAUC(mlp, downstreamTask, data)"""
        
        # Calculate weights and prediction for all sub_problems in eval_problem
        w_ij_eval, unique_clauses_eval, inverse_indices_eval = mlp.forward(downstreamTask, eval_problem, nodeToPred=node_to_predict)
        edge_ij_eval = mlp.sampleGraph(w_ij_eval, unique_clauses_eval, inverse_indices_eval, temperature).detach()
        #pSample_eval, _, _, _ = downstreamTask.forward(eval_problem, edge_weights=edge_ij_eval)
        #pOriginal_eval, _, _, _ = downstreamTask.forward(eval_problem)
        
        auroc_list = []
        
        for current_batch_num in range(len(eval_problem.is_sat)):
            # This can be repeated for each sub_problem
            clauses_current_problem = eval_problem.get_clauses_for_problem(current_batch_num)

            #print(f"Length of sub_problem 0: {len(clauses_current_problem)}")
            # Sub problem 1 Contains literals 11-20, ...
            #print(f"Sub_problem 0 clauses: {clauses_current_problem}")
            
            # Calculate mask for current sub_problem in eval_problem
            eval_batch_mask = utils.get_batch_mask(torch.tensor(eval_problem.batch_edges), batch_idx=current_batch_num, batch_size=opts['min_n'], n_variables=eval_problem.n_variables)
            
            # Edge probabilites for current sub problem in eval_problems
            edge_ij_eval_masked = edge_ij_eval[eval_batch_mask]
            
            sub_problem_edges = eval_problem.batch_edges[eval_batch_mask]
            
            #motif_size = len(gt_mask)
            
            curr_auroc = binary_auroc(edge_ij_eval_masked, reals[current_batch_num])
            auroc_list.append(curr_auroc.item())
            
        
        auroc_tensor = torch.tensor(auroc_list)
        mean_auroc = auroc_tensor.mean()
        if epoch == epochs-1:
            highest_auroc_index = torch.argmax(auroc_tensor)
            highest_mask = utils.get_batch_mask(torch.tensor(eval_problem.batch_edges), batch_idx=highest_auroc_index, batch_size=opts['min_n'], n_variables=eval_problem.n_variables)
            highest_auroc = auroc_tensor[highest_auroc_index]
            highest_edge_ij = edge_ij_eval[highest_mask]
            highest_gt = reals[highest_auroc_index]
            sub_problem_edges_highest = eval_problem.batch_edges[highest_mask]
            
            lowest_auroc_index = torch.argmin(auroc_tensor)
            lowest_mask = utils.get_batch_mask(torch.tensor(eval_problem.batch_edges), batch_idx=lowest_auroc_index, batch_size=opts['min_n'], n_variables=eval_problem.n_variables)
            lowest_auroc = auroc_tensor[lowest_auroc_index]
            lowest_edge_ij = edge_ij_eval[lowest_mask]
            lowest_gt = reals[lowest_auroc_index]
            sub_problem_edges_lowest = eval_problem.batch_edges[lowest_mask]
            
            # TODO: THIS REQUIRES PANDAS!
            #wandb.log({"highest-roc" : wandb.plot.roc_curve(highest_gt, highest_edge_ij,labels=None, classes_to_plot=None)})
                
        #weights_eval_masked = w_ij_eval[eval_batch_mask]
        #print(f"Edge weights for last sub_problem in last problem batch: {weights_eval_masked}")
        
        print(f"Edge probabilites for last sub_problem in last problem batch: {edge_ij_eval_masked}")
        
        #print(f"Prediction for sub_problem: {pOriginal_eval[0]}")
        #print(f"Prediction for sampled sub_problem: {pSample_eval[0]}")
        
        print(f"mean auroc score: {mean_auroc}")
    

        # TODO: VISUALIZE TOPK!
        # print sub_problem 0 with calculated edge weights
        if (epoch+1) % 5 == 0:
            pos = utils.visualize_edge_index_interactive(sub_problem_edges, edge_ij_eval_masked, f"results/replication/seed{runSeed}_vis_edge_ij_{epoch+1}", topK=len(gt_edges_per_problem[-1]))
        
        
        #sumSampledEdges = sumSampledEdges / len(training_iterator)
        #, "val/mean_AUC": meanAuc
        wandb.log({"train/Loss": loss, "val/temperature": temperature, "val/auroc": mean_auroc})

        """for name, param in mlp.named_parameters():
            if param.requires_grad:
                print(f"{name}: {param.grad}")"""
        
    # print sub_problem 0 with calculated edge weights
    pos = utils.visualize_edge_index_interactive(sub_problem_edges, edge_ij_eval_masked, f"results/replication/seed{runSeed}_vis_edge_ij_{epoch+1}", topK=len(gt_edges_per_problem[-1]))
    # print sub_problem 0 with gt
    pos = utils.visualize_edge_index_interactive(sub_problem_edges, reals[-1], f"results/replication/seed{runSeed}_vis_gt", pos)
    
    # TODO: Show difference between topK edges and gt edges -> logical and on topK and gt, visualize
    
    sorted_weights, topk_indices_highest = torch.topk(highest_edge_ij, len(gt_edges_per_problem[highest_auroc_index]))
    mask_topK_highest = torch.zeros_like(highest_edge_ij, dtype=torch.float32)
    mask_topK_highest[topk_indices_highest] = 1    
    
    common_edges_highest = torch.logical_and(highest_gt, mask_topK_highest.flatten())
    print(f"Highest individual auroc: {highest_auroc}")
    pos = utils.visualize_edge_index_interactive(sub_problem_edges_highest, highest_edge_ij, f"results/replication/seed{runSeed}_highestAUC", topK=len(gt_edges_per_problem[highest_auroc_index]))
    pos = utils.visualize_edge_index_interactive(sub_problem_edges_highest, highest_gt, f"results/replication/seed{runSeed}_highestAUC_gt")
    pos = utils.visualize_edge_index_interactive(sub_problem_edges_highest, common_edges_highest, f"results/replication/seed{runSeed}_highestAUC_commonEdges")
    
    # TO EVALUATE SATISFIABILITY OF EXPLANATION:
    print(f"Highest AUC example masked edges: {sub_problem_edges_highest[mask_topK_highest.bool()]}")
    
    # Group literals by clause number
    clause_dict = defaultdict(list)

    for literal, clause in sub_problem_edges_highest[mask_topK_highest.bool()]:
        literal = int(literal)
        clause = int(clause)
        if literal >= eval_problem.n_variables:
            literal = -(literal - eval_problem.n_variables)
        clause_dict[clause].append(literal)

    # Convert to list of clauses (optional: sort by clause number)
    clauses = list(clause_dict.values())
    
    print(clauses)
    
    # -----------------------------------
    
    sorted_highest_egde_ij, sorted_highest_indices = torch.sort(highest_edge_ij)
    x = list(range(len(sorted_highest_egde_ij)))
    
    kneedle = KneeLocator(x, sorted_highest_egde_ij.cpu().numpy(), S=1.0, curve="convex", direction="increasing")
    
    threshold_val = kneedle.knee_y
    
    knee_mask = highest_edge_ij >= threshold_val
    knee_masked_edge_ij_highest = highest_edge_ij[knee_mask]
    
    print(knee_masked_edge_ij_highest)
    
    clause_dict = defaultdict(list)

    for literal, clause in sub_problem_edges_highest[knee_mask.bool()]:
        literal = int(literal)
        clause = int(clause)
        if literal >= eval_problem.n_variables:
            literal = -(literal - eval_problem.n_variables)
        clause_dict[clause].append(literal)

    # Convert to list of clauses (optional: sort by clause number)
    clauses = list(clause_dict.values())
    
    print(f"Clauses calced with knee point: {clauses}")
    
    # -----------------------------------
    
    sorted_weights, topk_indices_lowest = torch.topk(lowest_edge_ij, len(gt_edges_per_problem[lowest_auroc_index]))
    mask_topK_lowest = torch.zeros_like(lowest_edge_ij, dtype=torch.float32)
    mask_topK_lowest[topk_indices_lowest] = 1
    
    common_edges_lowest = torch.logical_and(lowest_gt, mask_topK_lowest.flatten())
    print(f"Lowest individual auroc: {lowest_auroc}")
    pos = utils.visualize_edge_index_interactive(sub_problem_edges_lowest, lowest_edge_ij, f"results/replication/seed{runSeed}_lowestAUC", topK=len(gt_edges_per_problem[lowest_auroc_index]))
    pos = utils.visualize_edge_index_interactive(sub_problem_edges_lowest, lowest_gt, f"results/replication/seed{runSeed}_lowestAUC_gt")
    pos = utils.visualize_edge_index_interactive(sub_problem_edges_lowest, common_edges_lowest, f"results/replication/seed{runSeed}_lowestAUC_commonEdges")
    
        
    #if save_model == "True":
    #    torch.save(mlp.state_dict(), f"models/explainer_{dataset}_{meanAuc}_{wandb.run.name}")

    wandb.finish()
    
    return mlp, downstreamTask

In [3]:
datasetName="NeuroSAT"

In [6]:
for i in range(1):
    mlp, downstreamTask = trainExplainer(datasetName,opts, wandb_project="NeuroSAT-HARD-CONSTRAINT-HARD-SAMPLING-testroccurve", runSeed=i)

wandb: Using wandb-core as the SDK backend.  Please refer to https://wandb.me/wandb-core for more information.
wandb: Currently logged in as: tristan-schulz2001 (tristan-schulz2001-tu-dortmund) to https://api.wandb.ai. Use `wandb login --relogin` to force relogin


Downstream task accuracy on eval problem: 1.0
Epoch 1, Loss: 8.941383361816406
Edge probabilites for last sub_problem in last problem batch: tensor([0.5243, 0.5243, 0.5243, 0.5277, 0.5277, 0.5277, 0.5308, 0.5308, 0.5283,
        0.5283, 0.5283, 0.5283, 0.5283, 0.5283, 0.5283, 0.5283, 0.5258, 0.5258,
        0.5258, 0.5271, 0.5271, 0.5271, 0.5271, 0.5284, 0.5284, 0.5284, 0.5284,
        0.5284, 0.5235, 0.5235, 0.5235, 0.5169, 0.5169, 0.5169, 0.5258, 0.5258,
        0.5258, 0.5267, 0.5267, 0.5267, 0.5232, 0.5232, 0.5232, 0.5232, 0.5299,
        0.5299, 0.5299, 0.5229, 0.5229, 0.5229, 0.5229, 0.5229, 0.5229, 0.5229,
        0.5229, 0.5236, 0.5236, 0.5236, 0.5200, 0.5200, 0.5200, 0.5200, 0.5272,
        0.5272, 0.5272, 0.5272, 0.5272, 0.5272, 0.5255, 0.5255, 0.5255, 0.5247,
        0.5247, 0.5247, 0.5247, 0.5247, 0.5247, 0.5284, 0.5284, 0.5284, 0.5284,
        0.5284, 0.5284, 0.5284, 0.5284, 0.5279, 0.5279, 0.5279, 0.5279, 0.5279,
        0.5233, 0.5233, 0.5233, 0.5200, 0.5200, 0.5200, 0.5

wandb: ERROR The nbformat package was not found. It is required to save notebook history.


results/replication/seed0_highestAUC_commonEdges.html
Visualization saved as results/replication/seed0_highestAUC_commonEdges.html. Open it in your browser.
Highest AUC example masked edges: [[ 396 1180]
 [ 169 1180]
 [ 397 1181]
 [ 175 1181]
 [ 169 1181]
 [ 171 1187]
 [ 168 1191]
 [ 397 1191]
 [ 394 1191]
 [ 170 1193]
 [ 173 1193]
 [ 168 1193]
 [ 392 1194]
 [ 171 1194]
 [ 169 1195]
 [ 397 1195]
 [ 397 1201]
 [ 175 1201]
 [ 394 1201]
 [ 396 1201]
 [ 172 1202]
 [ 393 1202]
 [ 170 1202]
 [ 173 1202]
 [ 394 1210]
 [ 393 1210]
 [ 168 1213]
 [ 397 1213]
 [ 172 1217]
 [ 392 1217]
 [ 394 1217]
 [ 175 1221]
 [ 173 1221]
 [ 168 1221]]
[[-172, 169], [-173, 175, 169], [171], [168, -173, -170], [170, 173, 168], [-168, 171], [169, -173], [-173, 175, -170, -172], [172, -169, 170, 173], [-170, -169], [168, -173], [172, -168, -170], [175, 173, 168]]
tensor([6.9143e-07, 6.9143e-07, 5.4053e-07, 5.4053e-07, 5.4053e-07])
Clauses calced with knee point: [[-170, -169], [172, -168, -170]]
Lowest individual a

## Sweeping config

In [ ]:
"""sweep_config = {
    "method": 'grid',                    # random, grid or Bayesian search
    "metric": {"goal": "maximize", "name": "val/auroc"},
    "parameters": {
        'bce_loss': {
            'values': [0]           # Try 1
        },
        'epochs': {
            'values': [20, 30]
            },
        't0': {
            'values': [5.0]
            },
        'tT': {
            'values': [1.0, 5.0]
            },
        'sampled_graphs': {
            'values': [1, 5]            # Try 10
            },
        'size_reg': {
            'values': [1.0, 0.1]
            },
        'entropy_reg': {
            'values': [1.0, 0.1]
            },
        'L2_reg': {
            'values': [0.0]
            },
        'consistency_reg': {
            'values': [0.0]
            },
        'lr_mlp':{
            'values': [0.0003, 0.003, 0.01]
            },
        'complex_architecture': {
            'values': [1, 0]
        },
        'three_embs': {
            'values': [1, 0]
        },
        'seed':{
            'values': [75, 76]
            },
    },
}   """
sweep_config = {
    "method": 'grid',                    # random, grid or Bayesian search
    "metric": {"goal": "maximize", "name": "val/auroc"},
    "parameters": {
        'bce_loss': {
            'values': [0]           # Try 1
        },
        'epochs': {
            'values': [50, 70]
            },
        't0': {
            'values': [5.0]
            },
        'tT': {
            'values': [5.0]
            },
        'sampled_graphs': {
            'values': [5]            # Try 10
            },
        'size_reg': {
            'values': [1.0]
            },
        'entropy_reg': {
            'values': [1.0]
            },
        'L2_reg': {
            'values': [0.0]
            },
        'adamW': {
            'values': [0]
            },
        'consistency_reg': {
            'values': [0.0]
            },
        'lr_mlp':{
            'values': [0.01]
            },
        'complex_architecture': {
            'values': [1]
        },
        'three_embs': {
            'values': [1]
        },
        'seed':{
            'values': [75, 76]
            },
    },
}   

## Sweep Config Soft constraint

In [4]:
sweep_config = {
    "method": 'grid',                    # random, grid or Bayesian search
    "metric": {"goal": "maximize", "name": "val/auroc"},
    "parameters": {
        'bce_loss': {
            'values': [0]           # Try 1
        },
        'epochs': {
            'values': [20, 30, 50]
            },
        't0': {
            'values': [5.0]
            },
        'tT': {
            'values': [5.0]
            },
        'sampled_graphs': {
            'values': [5]            # Try 10
            },
        'size_reg': {
            'values': [0.001, 0.01]
            },
        'entropy_reg': {
            'values': [1.0, 0.1]
            },
        'L2_reg': {
            'values': [0.0]
            },
        'adamW': {
            'values': [0, 1]
            },
        'consistency_reg': {
            'values': [0.1, 1.0, 10.0]
            },
        'lr_mlp':{
            'values': [0.0003, 0.003]
            },
        'complex_architecture': {
            'values': [0]
        },
        'three_embs': {
            'values': [0, 1]
        },
        'seed':{
            'values': [75, 76]
            },
    },
}   

In [5]:
sweep_id = wandb.sweep(sweep_config, project="SWEEP-NeuroSAT-SOFT-CONSTRAINT-COMPLETE")

wandb: Using wandb-core as the SDK backend.  Please refer to https://wandb.me/wandb-core for more information.


Create sweep with ID: sjc6keu9
Sweep URL: https://wandb.ai/tristan-schulz2001-tu-dortmund/SWEEP-NeuroSAT-SOFT-CONSTRAINT-COMPLETE/sweeps/sjc6keu9


In [6]:
import sweepExplainerNeuroSAT

wandb.agent(sweep_id, sweepExplainerNeuroSAT.trainExplainer)

wandb: Agent Starting Run: 0n4t7qd7 with config:
wandb: 	L2_reg: 0
wandb: 	adamW: 0
wandb: 	bce_loss: 0
wandb: 	complex_architecture: 0
wandb: 	consistency_reg: 0.1
wandb: 	entropy_reg: 1
wandb: 	epochs: 20
wandb: 	lr_mlp: 0.0003
wandb: 	sampled_graphs: 5
wandb: 	seed: 75
wandb: 	size_reg: 0.001
wandb: 	t0: 5
wandb: 	tT: 5
wandb: 	three_embs: 0
wandb: Currently logged in as: tristan-schulz2001 (tristan-schulz2001-tu-dortmund) to https://api.wandb.ai. Use `wandb login --relogin` to force relogin


Epoch 1, Loss: 0.14864376187324524
mean auroc score: 0.5042453408241272
Epoch 2, Loss: 0.14820654690265656
mean auroc score: 0.5011637806892395
Epoch 3, Loss: 0.14828872680664062
mean auroc score: 0.4972538650035858
Epoch 4, Loss: 0.1477144956588745
mean auroc score: 0.4956935942173004
Epoch 5, Loss: 0.146976500749588
mean auroc score: 0.4950694441795349
Epoch 6, Loss: 0.14677414298057556
mean auroc score: 0.49364790320396423
Epoch 7, Loss: 0.14688740670681
mean auroc score: 0.4934850335121155
Epoch 8, Loss: 0.1462288200855255
mean auroc score: 0.492706835269928
Epoch 9, Loss: 0.1456499993801117
mean auroc score: 0.49106836318969727
Epoch 10, Loss: 0.1461312472820282
mean auroc score: 0.48901745676994324
Epoch 11, Loss: 0.14538268744945526
mean auroc score: 0.4872990548610687
Epoch 12, Loss: 0.14484450221061707
mean auroc score: 0.4856020510196686
Epoch 13, Loss: 0.1449875682592392
mean auroc score: 0.4849960505962372
Epoch 14, Loss: 0.14393272995948792
mean auroc score: 0.484733402729

wandb: ERROR The nbformat package was not found. It is required to save notebook history.


mean auroc score: 0.48146143555641174


wandb: Agent Starting Run: p9vic1ee with config:
wandb: 	L2_reg: 0
wandb: 	adamW: 0
wandb: 	bce_loss: 0
wandb: 	complex_architecture: 0
wandb: 	consistency_reg: 0.1
wandb: 	entropy_reg: 1
wandb: 	epochs: 20
wandb: 	lr_mlp: 0.0003
wandb: 	sampled_graphs: 5
wandb: 	seed: 75
wandb: 	size_reg: 0.001
wandb: 	t0: 5
wandb: 	tT: 5
wandb: 	three_embs: 1


...

wandb: Agent Starting Run: 70rv2w6f with config:
wandb: 	L2_reg: 0
wandb: 	adamW: 1
wandb: 	bce_loss: 0
wandb: 	complex_architecture: 0
wandb: 	consistency_reg: 10
wandb: 	entropy_reg: 0.1
wandb: 	epochs: 50
wandb: 	lr_mlp: 0.003
wandb: 	sampled_graphs: 5
wandb: 	seed: 76
wandb: 	size_reg: 0.01
wandb: 	t0: 5
wandb: 	tT: 5
wandb: 	three_embs: 1


Epoch 1, Loss: 2.689878225326538
mean auroc score: 0.4841073453426361
Epoch 2, Loss: 2.8951704502105713
mean auroc score: 0.47812026739120483
Epoch 3, Loss: 2.6165735721588135
mean auroc score: 0.48966869711875916
Epoch 4, Loss: 2.603178024291992
mean auroc score: 0.48588499426841736
Epoch 5, Loss: 2.5067646503448486
mean auroc score: 0.48198699951171875
Epoch 6, Loss: 2.4190354347229004
mean auroc score: 0.4792400002479553
Epoch 7, Loss: 2.2038142681121826
mean auroc score: 0.4766344428062439
Epoch 8, Loss: 2.0182974338531494
mean auroc score: 0.4764764606952667
Epoch 9, Loss: 1.8124570846557617
mean auroc score: 0.47676753997802734
Epoch 10, Loss: 1.6055465936660767
mean auroc score: 0.477109432220459
Epoch 11, Loss: 1.33521568775177
mean auroc score: 0.4774347245693207
Epoch 12, Loss: 1.1156500577926636
mean auroc score: 0.47768786549568176
Epoch 13, Loss: 0.860898494720459
mean auroc score: 0.4776909649372101
Epoch 14, Loss: 0.6456884145736694
mean auroc score: 0.4778425693511963
E

wandb: ERROR The nbformat package was not found. It is required to save notebook history.


mean auroc score: 0.47968053817749023


wandb: Sweep Agent: Waiting for job.
wandb: Sweep Agent: Exiting.
